In [141]:
#Bokeh plotting
from bokeh.io import push_notebook, show, output_notebook
from bokeh.plotting import figure
from bokeh.models import Span, Label, Arrow, NormalHead
from bokeh.models import HoverTool, tools, ColumnDataSource, CustomJS, Slider, BoxAnnotation
from bokeh.layouts import  column, row
from bokeh.palettes import Category20_18
import re
import glob, os
from astropy.io import fits
from urllib import urlretrieve
from pyraf import iraf
output_notebook()

Loading BokehJS ...

In [142]:
with open('../listA0.txt','r') as f:
    for lines in f:
        star = lines.split(',')[0]
        url= lines.split(',')[1]
        name = url.split('/')[-1]
        if not os.path.isfile(name.strip()):
            urlretrieve(url,name.strip())
        #print(url)

# Bokeh Plotting

In [143]:
#plot parameters
colors = Category20_18 #+ Viridis8 + Dark2_8 + Paired8 + Set1_4


xr = (5000,8900)
yr = (0,40)
p =  figure(x_axis_label='Angstrom', y_axis_label='Y',title="Click on the desired stellar template to overplot", x_range=xr, y_range=yr
              ,active_drag='pan', active_scroll='wheel_zoom',
              plot_width=900, plot_height=1000
             )

hover2 = HoverTool(
        tooltips=[
            ("(x,y)", "($x{1}, $y)"),
        ]
    )
p.add_tools(hover2)


for index,file in enumerate(glob.glob("spec*.fits")):
    ob = fits.open(file)
    dataob = ob[1].data
    
    x=10**(dataob['loglam'])
    y=dataob['flux']
    
    #If you want to have the name and not the spectra type change legend=name
    t = p.line(x=x,y=y,color=colors[index], line_alpha=1.0, 
           line_width=4,legend=ob[2].data['SUBCLASS'][0]+str(index),muted_alpha=0.,muted_color=colors[index])
    #This is a very ideficient way to have the colors in the legend to show up by default. 
#    t2 = p.line(x=x[0],y=y[0],color=colors[index], line_alpha=1.0, 
#           line_width=4,legend=ob[2].data['SUBCLASS'][0]+str(index),muted_alpha=1.,muted_color=colors[index])

    
    
    
    
#    t = p.line(x=10**(dataob['loglam']),y=dataob['model'], line_alpha=0.0, 
#           line_width=4,legend=ob[2].data['SUBCLASS'][0]+str(index),color=colors[i],muted_color=colors[i])
#    #This is a very ideficient way to have the colors in the legend to show up by default. 
#    t2 = p.line(x=10**(dataob['loglam']),y=dataob['model'], line_alpha=1.0, 
#           line_width=4,legend=ob[2].data['SUBCLASS'][0]+str(index),muted_alpha=1.,color=colors[i],muted_color=colors[i])


    
    
    
p.legend.location = "top_left"
p.legend.click_policy="mute"
show(p)

# Plotting the model not the data

In [144]:
#plot parameters
colors = Category20_18 #+ Viridis8 + Dark2_8 + Paired8 + Set1_4


xr = (5000,8900)
yr = (0,40)
p =  figure(x_axis_label='Angstrom', y_axis_label='Y',title="Click on the desired stellar template to overplot", x_range=xr, y_range=yr
              ,active_drag='pan', active_scroll='wheel_zoom',
              plot_width=900, plot_height=1000
             )

hover2 = HoverTool(
        tooltips=[
            ("(x,y)", "($x{1}, $y)"),
        ]
    )
p.add_tools(hover2)


#os.chdir("/mydir")
for index,file in enumerate(glob.glob("spec*.fits")):
    ob = fits.open(file)
    dataob = ob[1].data
    
    x=10**(dataob['loglam'])
    y=dataob['model']
    
    #If you want to have the name and not the spectra type change legend=name
    t = p.line(x=x,y=y,color=colors[index], line_alpha=1.0, 
           line_width=4,legend=ob[2].data['SUBCLASS'][0]+str(index),muted_alpha=0.,muted_color=colors[index])

    
    
    
p.legend.location = "top_left"
p.legend.click_policy="mute"
show(p)

# Table to IRAF 

To find a gaussian can use the iraf routine [fitprofs](http://stsdas.stsci.edu/cgi-bin/gethelp.cgi?fitprofs). To use this need to convert the SDSS tables to IRAF image spectra. 

In [149]:
#Parametest for the fit:
def find_nearest(array,value):
    idx = (np.abs(array-value)).argmin()
    return idx, array[idx]

def isDigit(x):
    try:
        float(x)
        return True
    except ValueError:
        return False
    
def gaussian(x, mu, sig,core):
    return core*np.exp(-np.power(x - mu, 2.) / (2 * np.power(sig, 2.)))


#Error
eeqwgs = []
errorparam = []
errorestimate = True


#plot parameters
colors = Category20_18 #+ Viridis8 + Dark2_8 + Paired8 + Set1_4


xr = (5000,8900)
yr = (0,40)
pl =  figure(x_axis_label='Angstrom', y_axis_label='Y',title="Click on the desired stellar template to overplot", x_range=xr, y_range=yr
              ,active_drag='pan', active_scroll='wheel_zoom',
              plot_width=900, plot_height=1000
             )

hover2 = HoverTool(
        tooltips=[
            ("(x,y)", "($x{1}, $y)"),
        ]
    )
pl.add_tools(hover2)




for index,filename in enumerate(glob.glob("spec*.fits")):
    #import fits
    ob = fits.open(filename)
    #Get data and save wavelenft in x, and flux on y
    dataob = ob[1].data
    x = 10**(dataob['loglam'])
    y = dataob['model']

    #save to a .txt file
    namenewfits = '{name}.txt'.format(name=filename.split('.')[0])
    with open(namenewfits,'w') as file:
        for i in zip(x,y):
            file.write('{}\t{}\n'.format(i[0],i[1]))
    #Create fits file from text file interpolation. 
    iraffitsname = 'iraf'+filename.split('.')[0]
    if os.path.exists(iraffitsname+'.fits'):
        os.remove(iraffitsname+'.fits')

    iraf.noao.onedspec()
    iraf.dataio()
    iraf.rspectext(namenewfits,iraffitsname,dtype='interp')
    
    

    line = [8543,8598.,6562]
    regionfit = [[8520,8560],[8582,8609],[6550,6575]]

    #Initialize files log and lines
    ! echo '' > fited.log
    

    for lines in zip(line,regionfit):
        regionf = "{} {}".format(lines[1][0],lines[1][1])
        #wavelenght
        xlimns = [find_nearest(x,i)[0] for i in lines[1]    ]
        wavex = x[xlimns[0]:xlimns[1]]
        lineszero = lines[0]
        ! echo '$lineszero' > lines.lines
        
        filename = iraffitsname
        
        if errorestimate == True:        
            iraf.fitprofs(filename,pos='lines.lines', reg=regionf ,
                          fitbackground= 'yes', 
                          logfile='fited.log'
                          ,nerrsample='100',sigma0='4',invgain='4')
        else:
            iraf.fitprofs(filename,pos='lines.lines', reg=regionf ,
                          fitbackground= 'yes', 
                          logfile='fited.log')
            


        #Plotting the gaussian
        #Find in log file  
        npattern = re.compile('[-\d.]+')
        npattern2 = re.compile('[-\d.E?]+')

        gparameters=[]
        with open('fited.log','r') as file:
            for lines in file:
                
                if '(' not in lines:
                    temp = npattern2.findall(lines)
                    if 'INDEF' in lines:
                        gparameters.append(7*[0])
                else:
                    errorparam.append(npattern2.findall(lines))
                    
                if len(temp) == 7 and all(isDigit(i) for i in temp) and 'INDEF' not in lines:
                    gparameters.append(temp)

        #gaussian
        if len(gparameters) > 0:
            gparamfinal = [ float(i) for i in gparameters[-1] ]
            centerg, contg, fluxg, eqwg, coreg, fwhmg, fwhml = gparamfinal
            yg = gaussian(wavex,centerg,fwhmg/2.3538,coreg) + contg
            

        if errorestimate == True:
            errorparamfinal = [ float(i) for i in errorparam[-1] ]
            print(gparamfinal)
            print(errorparamfinal)

            #Plot
            #sourceg = ColumnDataSource(data=dict(x=wavex,y=yg))
            #pl.line(wavex,yg,color=colors[index], line_alpha=1.0, 
         
                    
                    #color=colors[index], line_alpha=1.0, 
                   #line_width=4,muted_alpha=0.,muted_color=colors[index])
            pl.line(wavex,yg,color='red', line_alpha=1., 
                line_width=5,legend=ob[2].data['SUBCLASS'][0]+str(index),muted_alpha=0.,muted_color=colors[index])



    #If you want to have the name and not the spectra type change legend=name
            t = pl.line(x=x,y=y,color=colors[index], line_alpha=1.0, 
                   line_width=4,legend=ob[2].data['SUBCLASS'][0]+str(index),muted_alpha=0.,muted_color=colors[index])


            
            message = 'type:{sclass},center:{cent},eqw:{eq}({eqer})'
            
                           
            eeqwgs.append([message.format(sclass = ob[2].data['SUBCLASS'][0]+str(index),
                           cent = centerg
                           ,eq = eqwg
                           ,eqer = errorparamfinal[3])])

    
    
pl.legend.location = "top_left"
pl.legend.click_policy="mute"

show(pl)           

# Jan 28 18:19 irafspec-0266-51602-0014 - Ap 1: 
# Nfit=1, background=yes, positions=all, gfwhm=all, lfwhm=all
#   center      cont      flux       eqw      core     gfwhm     lfwhm
  8551.979  9.978109   -12.091     1.212  -1.09642     10.36        0.
 ( 48.332) (2.90707) (497.838) (  31.34) (21.1108) (  60.18) (     0.)
[8551.979, 9.978109, -12.091, 1.212, -1.09642, 10.36, 0.0]
[48.332, 2.90707, 497.838, 31.34, 21.1108, 60.18, 0.0]
# Jan 28 18:19 irafspec-0266-51602-0014 - Ap 1: 
# Nfit=1, background=yes, positions=all, gfwhm=all, lfwhm=all
#   center      cont      flux       eqw      core     gfwhm     lfwhm
  8594.965 -202.3151   167570.     INDEF   211.978     742.6        0.
 (2952.15) (389.558) (9.168E8) (     0.) (477.528) (1.442E6) (     0.)
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
[2952.15, 389.558, 916800000.0, 0.0, 477.528, 1442000.0, 0.0]
# Jan 28 18:19 irafspec-0266-51602-0014 - Ap 1: 


/home/mmarcano/anaconda3/envs/iraf27/lib/python2.7/site-packages/ipykernel_launcher.py:14: RuntimeWarning: divide by zero encountered in divide
  


# Nfit=1, background=yes, positions=all, gfwhm=all, lfwhm=all
#   center      cont      flux       eqw      core     gfwhm     lfwhm
  6568.844  14.51048  -20.3878     1.405  -2.84271     6.738        0.
 (21.3345) (  4.862) (430.086) (   17.9) (24.0457) (  30.14) (     0.)
[6568.844, 14.51048, -20.3878, 1.405, -2.84271, 6.738, 0.0]
[21.3345, 4.862, 430.086, 17.9, 24.0457, 30.14, 0.0]
# Jan 28 18:19 irafspec-0266-51602-0084 - Ap 1: 
# Nfit=1, background=yes, positions=all, gfwhm=all, lfwhm=all
#   center      cont      flux       eqw      core     gfwhm     lfwhm
  8548.364  14.09451  -10.3952    0.7375 -0.993874     9.826        0.
 (51.5547) (2.53817) (225.287) (  10.16) (29.1073) (  56.41) (     0.)
[8548.364, 14.09451, -10.3952, 0.7375, -0.993874, 9.826, 0.0]
[51.5547, 2.53817, 225.287, 10.16, 29.1073, 56.41, 0.0]
# Jan 28 18:19 irafspec-0266-51602-0084 - Ap 1: 
# Nfit=1, background=yes, positions=all, gfwhm=all, lfwhm=all
#   center      cont      flux       eqw      core     gfwh

# Jan 28 18:20 irafspec-0266-51602-0397 - Ap 1: 
# Nfit=1, background=yes, positions=all, gfwhm=all, lfwhm=all
#   center      cont      flux       eqw      core     gfwhm     lfwhm
  8544.033  4.352672  -5.74463      1.32 -0.539856     9.997        0.
 (116.208) (2.61178) (3392.79) (  58.85) (31.1031) (  85.15) (     0.)
[8544.033, 4.352672, -5.74463, 1.32, -0.539856, 9.997, 0.0]
[116.208, 2.61178, 3392.79, 58.85, 31.1031, 85.15, 0.0]
# Jan 28 18:20 irafspec-0266-51602-0397 - Ap 1: 
# Nfit=1, background=yes, positions=all, gfwhm=all, lfwhm=all
#   center      cont      flux       eqw      core     gfwhm     lfwhm
  8596.954  4.303778  -5.69831     1.324 -0.383514     13.96        0.
 (339.267) (3.70291) (10414.4) (  99.36) (27.9356) (  332.9) (     0.)
[8596.954, 4.303778, -5.69831, 1.324, -0.383514, 13.96, 0.0]
[339.267, 3.70291, 10414.4, 99.36, 27.9356, 332.9, 0.0]
# Jan 28 18:20 irafspec-0266-51602-0397 - Ap 1: 
# Nfit=1, background=yes, positions=all, gfwhm=all, lfwhm=all
#   cent

[8545.594, 2.810748, -2.56832, 0.9138, -0.249284, 9.679, 0.0]
[262.732, 1.82635, 1270.11, 88.06, 13.6734, 112.1, 0.0]
# Jan 28 18:20 irafspec-0266-51602-0500 - Ap 1: 
# Nfit=1, background=yes, positions=all, gfwhm=all, lfwhm=all
#   center      cont      flux       eqw      core     gfwhm     lfwhm
  8597.746  2.765074  -2.27072    0.8212 -0.160975     13.25        0.
 (324.358) ( 2.2899) (2481.73) (  73.73) (24.7113) (   145.) (     0.)
[8597.746, 2.765074, -2.27072, 0.8212, -0.160975, 13.25, 0.0]
[324.358, 2.2899, 2481.73, 73.73, 24.7113, 145.0, 0.0]
# Jan 28 18:20 irafspec-0266-51602-0500 - Ap 1: 
# Nfit=1, background=yes, positions=all, gfwhm=all, lfwhm=all
#   center      cont      flux       eqw      core     gfwhm     lfwhm
  6564.314  4.333961  -6.84959      1.58 -0.810198     7.942        0.
 (75.1611) (5.87532) (3227.35) (  74.86) (34.5147) (  65.42) (     0.)
[6564.314, 4.333961, -6.84959, 1.58, -0.810198, 7.942, 0.0]
[75.1611, 5.87532, 3227.35, 74.86, 34.5147, 65.42, 0.0]
#

In [150]:
eeqwgs

[['type:A00,center:8551.979,eqw:1.212(31.34)'],
 ['type:A00,center:0.0,eqw:0.0(0.0)'],
 ['type:A00,center:6568.844,eqw:1.405(17.9)'],
 ['type:A01,center:8548.364,eqw:0.7375(10.16)'],
 ['type:A01,center:8600.945,eqw:0.6898(23.95)'],
 ['type:A01,center:6566.232,eqw:1.06(12.8)'],
 ['type:A02,center:8550.633,eqw:1.709(4.972)'],
 ['type:A02,center:8604.046,eqw:1.728(25.67)'],
 ['type:A02,center:6568.031,eqw:2.335(3.069)'],
 ['type:A03,center:8542.942,eqw:1.154(3.349)'],
 ['type:A03,center:8595.844,eqw:1.142(30.94)'],
 ['type:A03,center:6562.378,eqw:1.775(2.131)'],
 ['type:A04,center:8552.642,eqw:0.6704(35.92)'],
 ['type:A04,center:8590.522,eqw:-0.3272(91.77)'],
 ['type:A04,center:6563.749,eqw:457.8(40253.0)'],
 ['type:A05,center:8548.111,eqw:0.7512(21.9)'],
 ['type:A05,center:8600.341,eqw:0.5783(102.4)'],
 ['type:A05,center:6566.081,eqw:1.162(28.41)'],
 ['type:A06,center:0.0,eqw:0.0(0.0)'],
 ['type:A06,center:8605.279,eqw:0.5168(22.67)'],
 ['type:A06,center:6568.938,eqw:0.8589(2.823)'],
 ['